# Kolokwium poprawkowe  
27.01.2020

### Proszę zmienić nazwę tego notebooka na następującą postać: AS_Kolokwium_Poprawkowe_numer_indeksu.ipynb, wpisując we właściwym miejscu własny numer indeksu.

_Rozwiązania proszę odesłać na adres jarekz@fuw.edu.pl_


Importy i funkcje, które przydadzą się do rozwiązania zadania, treści zadań znajdują się poniżej.

In [ ]:
import numpy as np
import matplotlib.pylab as plt
import scipy.signal as ss

In [ ]:
def charkterystyki(a,b,f,T,Fs):
    t = np.arange(-T, T, 1/Fs)
    
    f, h = ss.freqz(b, a, worN= f, fs = Fs) 
    m = np.abs(h)
    
    f, grupowe = ss.group_delay((b,a), w=f, fs = Fs)
    
    fig = plt.figure()
    plt.subplot(2,2,1)
    plt.title('moduł transmitancji')
    plt.plot(f,20*np.log10(m))
    plt.ylabel('[dB]')
    plt.ylim([-20, 1])
    plt.grid(True)
    
    plt.subplot(2,2,3)
    plt.title('opóźnienie grupowe')
    plt.plot(f,grupowe)
    plt.ylabel('próbki')
    plt.xlabel('Częstość [Hz]')
    plt.grid(True)
    plt.ylim([0, np.max(grupowe)+1])
    
    plt.subplot(2,2,2)
    plt.title('odpowiedź impulsowa')
    x = np.zeros(len(t))
    x[len(t)//2] = 1
    y = ss.lfilter(b,a,x)
    plt.plot(t, x)
    plt.plot(t, y)
    plt.xlim([-T/2,T])
    plt.grid(True)
    
    plt.subplot(2,2,4)
    plt.title('odpowiedź schodkowa')
    s = np.zeros(len(t))
    s[len(t)//2:] = 1
    ys = ss.lfilter(b,a,s) 
    plt.plot(t, s)
    plt.plot(t, ys)
    plt.xlim([-T/2,T])
    plt.xlabel('Czas [s]')
    plt.grid(True)
    
    fig.subplots_adjust(hspace=.5)
    plt.show()

In [ ]:
def parametryAR(x,p):
    '''funkcja estymująca parametry modelu AR 
    argumenty:
    x - sygnał
    p - rząd modelu
    f. zwraca:
    a - wektor współczynników modelu
    epsilon - estymowana wariancja szumu

    funkcja wymaga zaimportowania modułu numpy as np
    '''
    N = len(x)
    ak = np.correlate(x,x,mode='full')
    norm_ak = np.hstack((np.arange(1,N+1,1),np.arange(N-1,0,-1)))
    ak=ak/norm_ak
    R=ak[N-1:]
    RL  = R[1:1+p]
    RP = np.zeros((p,p))
    for i in range(p):
        aa = ak[N-1-i:N-1-i+p]
        RP[i,:] = aa
    a=np.linalg.solve(RP,RL)
    sigma2 = (ak[N-1] - np.sum(a*ak[N:N+p]))
    return a, sigma2

In [ ]:
def TFRPlot(TFR, t_mapy, f_mapy, sig, Fs=128,title =''):
    '''
    Funkcja do rysowania map czas-częstość z sygnałem zaprezentowanym poniżej
    TFR - mapa czas-częstość (time-freqyency representation
    t_mapy, f_mapy - wektory reprezentujące osie czasu i częstości
    sig - sygnał do wyrysowania pod mapą (np. ten, z którego powstała mapa)
    Fs - częstość próbkowania sygnału 
    title - tytuł do wyświetlenia ponad mapą
    '''
    df = f_mapy[1]-f_mapy[0]
    dt = t_mapy[1]-t_mapy[0]
    t = np.arange(0,len(sig))/Fs
    
    plt.figure()
    sygAxes = plt.axes([0.05, 0.05, 0.8, 0.1])
    tfAxes = plt.axes([0.05, 0.15, 0.8, 0.8])
    sygAxes.plot(t,sig)
    plt.xlim((t_mapy.min(), t_mapy.max()))
    #plt.setp(sygAxes, yticklabels=[])
    tfAxes.imshow(TFR,aspect='auto',origin='lower',interpolation='nearest', 
                  extent=(t_mapy.min()-dt/2,t_mapy.max()+dt/2,f_mapy.min()-df/2,f_mapy.max()+df/2))
    plt.setp(tfAxes,xticklabels=[])
    plt.title(title)
    plt.show()
    

### Zadanie 1.  Procesy AR (5pkt)

#### Proszę wczytać plik 
https://www.fuw.edu.pl/~jarekz/KOLOKWIUM_AS/zad1_syg.bin 

Jest to sygnał jednokanałowy, liczby są zapisane w formacie ‘<f’, próbkowanie 128Hz. Proszę wczytać sygnał i wykreślić jego przebieg.

#### Proszę napisać funkcję tworzącą wykres AIC. (1pkt)
Dla przypomnienia, kryterium Akaike (AIC):

  $\mathrm{AIC}(p)= \frac{2p}{N} +\ln(V) $

$p$ - liczba parametrów modelu, $N$ - liczba próbek sygnału,$V$ - wariancja szumu.

#### Proszę wybrać optymalny rząd na podstawie wykresu i uzasadnić swój wybór (1pkt)

Miejsce na komentarz

#### Proszę wyestymować współczynniki modelu AR dla wybranego rzędu, a następnie obliczyć widmo modelu AR (1pkt)

#### Proszę skomentować otrzymane wyniki (1pkt)

### Zadanie 2. Filtrowanie sygnałów (6pkt)

#### Proszę wczytać plik 
https://www.fuw.edu.pl/~jarekz/KOLOKWIUM_AS/zad2_syg.bin

Jest to sygnał jednokanałowy, liczby są zapisane w formacie ‘float64’, próbkowanie 128Hz. Proszę wykreślić jego przebieg. Jest to sygnał złożony z 2 gaborów o częstości 10Hz i skali 1s, delty oraz szumu.

#### Skonstruuj dwa projekty filtra, o zadanych parametrach (2pkt):
- Filtr Chebyshev II dla pasma przenoszenia 9-11Hz, z pasmem przejściowym o długości 1Hz, tak by minimalne tłumienie w paśmie zaporowym wynosiło 25 dB.

- Filtr pasmowo przepustowy Butterworth’a 3 rzędu z wartościami odcięcia 8 i 12 Hz.

#### Wraz z projektem filtra proszę wyrysować jego charakterystyki (0,5pkt)

#### Proszę zastosować filtr do wczytanego sygnału (1pkt)

#### Proszę skomentować wynik (3pkt)

### Zadanie 3. Mapy czas częstość (5pkt)
Przydatna funkcja:

#### Proszę uzupełnić funkcje spektrogram (2pkt)

In [ ]:
def spektrogram(x, okno, trans , Fs):
    Nx = len(x)
    No = len(okno)
    okno = #unormuj okno
    pozycje_okna = np.arange(0, Nx, trans)                        
    t = pozycje_okna/Fs
    N_trans = len(pozycje_okna)    
    f = np.fft.rfftfreq(No, 1/Fs)
    P = np.zeros((len(f),N_trans))
    z = np.zeros(int(No/2))
    sig = np.concatenate((z,x,z))
    for i,poz in enumerate(pozycje_okna):
        s = sig[poz:...]
        s = s*okno 
        S = ...
        P_tmp = ...   
        P_tmp = P_tmp.real/Fs 
        if len(s)%2 ==0: # dokładamy moc z ujemnej części widma 
            P_tmp[1:-1] *=2
        else:
            P_tmp[1:] *=2            
        P[:,i] = P_tmp
    return t,f,P

####  Proszę wczytać plik o nazwie 
https://www.fuw.edu.pl/~jarekz/KOLOKWIUM_AS/zad3_syg.bin

#### Jest to sygnał jednokanałowy, liczby są zapisane w formacie ‘float’, próbkowanie 128Hz. Proszę wykreślić jego przebieg.

#### Proszę wywołać spektrogram dla sygnału 'zad3_syg.bin' dla różnych długości okien i skomentować jaki mają wpływ na rozdzielczość czasową i przestrzenną (2pkt)

### Zadanie 4. Własności okienek i periodogram (5pkt)

#### Proszę wczytać plik 

https://www.fuw.edu.pl/~jarekz/KOLOKWIUM_AS/zad4_syg.bin

#### Jest to sygnał jednokanałowy, liczby są zapisane w formacie  ‘<f’, próbkowanie 100Hz. Proszę wykreślić jego przebieg

#### Proszę wykreślić periodogram okienka i zokienkowanego sygnału dla okna prostokątnego i hamming’a w skali decybelowej; widma okienek wyestymować dla `nfft = 1024` (2pkt)

#### Skomentowac różnice pomiędzy otrzymanymi widmami w oparciu i tw. o splocie (3pkt) 
